In [2]:
import nibabel as nib
import numpy as np
import os
import nrrd
import shutil
from cv2 import resize
import matplotlib.pyplot as plt
from PIL import Image
import torch
import torchvision.transforms as transforms
from tqdm import tqdm
%matplotlib inline

In [3]:
TRAIN_PATH = 'HACKATHON/images/train/'
TEST_PATH = 'HACKATHON/images/test/'
SEGMENTATION_PATH = 'HACKATHON/segmentations/train/'
LABEL_PATH = 'HACKATHON/train.txt'

In [4]:
from models import semi, infnet

In [5]:
import torch.nn as nn
import math
import torch.utils.model_zoo as model_zoo
import torch
import torch.nn.functional as F

__all__ = ['Res2Net', 'res2net50_v1b', 'res2net101_v1b', 'res2net50_v1b_26w_4s']

model_urls = {
    'res2net50_v1b_26w_4s': 'https://shanghuagao.oss-cn-beijing.aliyuncs.com/res2net/res2net50_v1b_26w_4s-3cf99910.pth',
    'res2net101_v1b_26w_4s': 'https://shanghuagao.oss-cn-beijing.aliyuncs.com/res2net/res2net101_v1b_26w_4s-0812c246.pth',
}


class Bottle2neck(nn.Module):
    expansion = 4

    def __init__(self, inplanes, planes, stride=1, downsample=None, baseWidth=26, scale=4, stype='normal'):
        """ Constructor
        Args:
            inplanes: input channel dimensionality
            planes: output channel dimensionality
            stride: conv stride. Replaces pooling layer.
            downsample: None when stride = 1
            baseWidth: basic width of conv3x3
            scale: number of scale.
            type: 'normal': normal set. 'stage': first block of a new stage.
        """
        super(Bottle2neck, self).__init__()

        width = int(math.floor(planes * (baseWidth / 64.0)))
        self.conv1 = nn.Conv2d(inplanes, width * scale, kernel_size=1, bias=False)
        self.bn1 = nn.BatchNorm2d(width * scale)

        if scale == 1:
            self.nums = 1
        else:
            self.nums = scale - 1
        if stype == 'stage':
            self.pool = nn.AvgPool2d(kernel_size=3, stride=stride, padding=1)
        convs = []
        bns = []
        for i in range(self.nums):
            convs.append(nn.Conv2d(width, width, kernel_size=3, stride=stride, padding=1, bias=False))
            bns.append(nn.BatchNorm2d(width))
        self.convs = nn.ModuleList(convs)
        self.bns = nn.ModuleList(bns)

        self.conv3 = nn.Conv2d(width * scale, planes * self.expansion, kernel_size=1, bias=False)
        self.bn3 = nn.BatchNorm2d(planes * self.expansion)

        self.relu = nn.ReLU(inplace=True)
        self.downsample = downsample
        self.stype = stype
        self.scale = scale
        self.width = width

    def forward(self, x):
        residual = x

        out = self.conv1(x)
        out = self.bn1(out)
        out = self.relu(out)

        spx = torch.split(out, self.width, 1)
        for i in range(self.nums):
            if i == 0 or self.stype == 'stage':
                sp = spx[i]
            else:
                sp = sp + spx[i]
            sp = self.convs[i](sp)
            sp = self.relu(self.bns[i](sp))
            if i == 0:
                out = sp
            else:
                out = torch.cat((out, sp), 1)
        if self.scale != 1 and self.stype == 'normal':
            out = torch.cat((out, spx[self.nums]), 1)
        elif self.scale != 1 and self.stype == 'stage':
            out = torch.cat((out, self.pool(spx[self.nums])), 1)

        out = self.conv3(out)
        out = self.bn3(out)

        if self.downsample is not None:
            residual = self.downsample(x)

        out += residual
        out = self.relu(out)

        return out


class Res2Net(nn.Module):

    def __init__(self, block, layers, baseWidth=26, scale=4, num_classes=1000):
        self.inplanes = 64
        super(Res2Net, self).__init__()
        self.baseWidth = baseWidth
        self.scale = scale
        self.conv1 = nn.Sequential(
            nn.Conv2d(3, 32, 3, 2, 1, bias=False),
            nn.BatchNorm2d(32),
            nn.ReLU(inplace=True),
            nn.Conv2d(32, 32, 3, 1, 1, bias=False),
            nn.BatchNorm2d(32),
            nn.ReLU(inplace=True),
            nn.Conv2d(32, 64, 3, 1, 1, bias=False)
        )
        self.bn1 = nn.BatchNorm2d(64)
        self.relu = nn.ReLU()
        self.maxpool = nn.MaxPool2d(kernel_size=3, stride=2, padding=1)
        self.layer1 = self._make_layer(block, 64, layers[0])
        self.layer2 = self._make_layer(block, 128, layers[1], stride=2)
        self.layer3 = self._make_layer(block, 256, layers[2], stride=2)
        self.layer4 = self._make_layer(block, 512, layers[3], stride=2)
        self.avgpool = nn.AdaptiveAvgPool2d(1)
        self.fc = nn.Linear(512 * block.expansion, num_classes)

        for m in self.modules():
            if isinstance(m, nn.Conv2d):
                nn.init.kaiming_normal_(m.weight, mode='fan_out', nonlinearity='relu')
            elif isinstance(m, nn.BatchNorm2d):
                nn.init.constant_(m.weight, 1)
                nn.init.constant_(m.bias, 0)

    def _make_layer(self, block, planes, blocks, stride=1):
        downsample = None
        if stride != 1 or self.inplanes != planes * block.expansion:
            downsample = nn.Sequential(
                nn.AvgPool2d(kernel_size=stride, stride=stride,
                             ceil_mode=True, count_include_pad=False),
                nn.Conv2d(self.inplanes, planes * block.expansion,
                          kernel_size=1, stride=1, bias=False),
                nn.BatchNorm2d(planes * block.expansion),
            )

        layers = []
        layers.append(block(self.inplanes, planes, stride, downsample=downsample,
                            stype='stage', baseWidth=self.baseWidth, scale=self.scale))
        self.inplanes = planes * block.expansion
        for i in range(1, blocks):
            layers.append(block(self.inplanes, planes, baseWidth=self.baseWidth, scale=self.scale))

        return nn.Sequential(*layers)

    def forward(self, x):
        x = self.conv1(x)
        x = self.bn1(x)
        x = self.relu(x)
        x = self.maxpool(x)

        x = self.layer1(x)
        x = self.layer2(x)
        x = self.layer3(x)
        x = self.layer4(x)

        x = self.avgpool(x)
        x = x.view(x.size(0), -1)
        x = self.fc(x)

        return x


def res2net50_v1b(pretrained=False, **kwargs):
    """Constructs a Res2Net-50_v1b model_lung_infection.
    Res2Net-50 refers to the Res2Net-50_v1b_26w_4s.
    Args:
        pretrained (bool): If True, returns a model_lung_infection pre-trained on ImageNet
    """
    model = Res2Net(Bottle2neck, [3, 4, 6, 3], baseWidth=26, scale=4, **kwargs)
    if pretrained:
        model.load_state_dict(model_zoo.load_url(model_urls['res2net50_v1b_26w_4s']),map_location=torch.device('cpu') )
    return model


def res2net101_v1b(pretrained=False, **kwargs):
    """Constructs a Res2Net-50_v1b_26w_4s model_lung_infection.
    Args:
        pretrained (bool): If True, returns a model_lung_infection pre-trained on ImageNet
    """
    model = Res2Net(Bottle2neck, [3, 4, 23, 3], baseWidth=26, scale=4, **kwargs)
    if pretrained:
        model.load_state_dict(model_zoo.load_url(model_urls['res2net101_v1b_26w_4s']))
    return model


def res2net50_v1b_26w_4s(pretrained=True, **kwargs):
    """Constructs a Res2Net-50_v1b_26w_4s model_lung_infection.
    Args:
        pretrained (bool): If True, returns a model_lung_infection pre-trained on ImageNet
    """
    model = Res2Net(Bottle2neck, [3, 4, 6, 3], baseWidth=26, scale=4, **kwargs)
    if pretrained:
        # Please replace it with your custom path
        model_state = torch.load('res2net50_v1b_26w_4s-3cf99910.pth', map_location=torch.device('cpu'))
        model.load_state_dict(model_state)
        # model_lung_infection.load_state_dict(model_zoo.load_url(model_urls['res2net50_v1b_26w_4s']))
    return model


def res2net101_v1b_26w_4s(pretrained=False, **kwargs):
    """Constructs a Res2Net-50_v1b_26w_4s model_lung_infection.
    Args:
        pretrained (bool): If True, returns a model_lung_infection pre-trained on ImageNet
    """
    model = Res2Net(Bottle2neck, [3, 4, 23, 3], baseWidth=26, scale=4, **kwargs)
    if pretrained:
        model.load_state_dict(model_zoo.load_url(model_urls['res2net101_v1b_26w_4s']))
    return model


def res2net152_v1b_26w_4s(pretrained=False, **kwargs):
    """Constructs a Res2Net-50_v1b_26w_4s model_lung_infection.
    Args:
        pretrained (bool): If True, returns a model_lung_infection pre-trained on ImageNet
    """
    model = Res2Net(Bottle2neck, [3, 8, 36, 3], baseWidth=26, scale=4, **kwargs)
    if pretrained:
        model.load_state_dict(model_zoo.load_url(model_urls['res2net152_v1b_26w_4s']))
    return model

import torch
import torch.nn as nn
import torch.nn.functional as F


class BasicConv2d(nn.Module):
    def __init__(self, in_planes, out_planes, kernel_size, stride=1, padding=0, dilation=1):
        super(BasicConv2d, self).__init__()
        self.conv = nn.Conv2d(in_planes, out_planes,
                              kernel_size=kernel_size, stride=stride,
                              padding=padding, dilation=dilation, bias=False)
        self.bn = nn.BatchNorm2d(out_planes)
        self.relu = nn.ReLU(inplace=True)

    def forward(self, x):
        x = self.conv(x)
        x = self.bn(x)
        return x


class RFB_modified(nn.Module):
    def __init__(self, in_channel, out_channel):
        super(RFB_modified, self).__init__()
        self.relu = nn.ReLU(True)
        self.branch0 = nn.Sequential(
            BasicConv2d(in_channel, out_channel, 1),
        )
        self.branch1 = nn.Sequential(
            BasicConv2d(in_channel, out_channel, 1),
            BasicConv2d(out_channel, out_channel, kernel_size=(1, 3), padding=(0, 1)),
            BasicConv2d(out_channel, out_channel, kernel_size=(3, 1), padding=(1, 0)),
            BasicConv2d(out_channel, out_channel, 3, padding=3, dilation=3)
        )
        self.branch2 = nn.Sequential(
            BasicConv2d(in_channel, out_channel, 1),
            BasicConv2d(out_channel, out_channel, kernel_size=(1, 5), padding=(0, 2)),
            BasicConv2d(out_channel, out_channel, kernel_size=(5, 1), padding=(2, 0)),
            BasicConv2d(out_channel, out_channel, 3, padding=5, dilation=5)
        )
        self.branch3 = nn.Sequential(
            BasicConv2d(in_channel, out_channel, 1),
            BasicConv2d(out_channel, out_channel, kernel_size=(1, 7), padding=(0, 3)),
            BasicConv2d(out_channel, out_channel, kernel_size=(7, 1), padding=(3, 0)),
            BasicConv2d(out_channel, out_channel, 3, padding=7, dilation=7)
        )
        self.conv_cat = BasicConv2d(4*out_channel, out_channel, 3, padding=1)
        self.conv_res = BasicConv2d(in_channel, out_channel, 1)

    def forward(self, x):
        x0 = self.branch0(x)
        x1 = self.branch1(x)
        x2 = self.branch2(x)
        x3 = self.branch3(x)
        x_cat = self.conv_cat(torch.cat((x0, x1, x2, x3), 1))

        x = self.relu(x_cat + self.conv_res(x))
        return x


class aggregation(nn.Module):
    # dense aggregation, it can be replaced by other aggregation previous, such as DSS, amulet, and so on.
    # used after MSF
    def __init__(self, channel, n_class):
        super(aggregation, self).__init__()
        self.relu = nn.ReLU(True)

        self.upsample = nn.Upsample(scale_factor=2, mode='bilinear', align_corners=True)
        self.conv_upsample1 = BasicConv2d(channel, channel, 3, padding=1)
        self.conv_upsample2 = BasicConv2d(channel, channel, 3, padding=1)
        self.conv_upsample3 = BasicConv2d(channel, channel, 3, padding=1)
        self.conv_upsample4 = BasicConv2d(channel, channel, 3, padding=1)
        self.conv_upsample5 = BasicConv2d(2*channel, 2*channel, 3, padding=1)

        self.conv_concat2 = BasicConv2d(2*channel, 2*channel, 3, padding=1)
        self.conv_concat3 = BasicConv2d(3*channel, 3*channel, 3, padding=1)
        self.conv4 = BasicConv2d(3*channel, 3*channel, 3, padding=1)
        self.conv5 = nn.Conv2d(3*channel, n_class, 1)

    def forward(self, x1, x2, x3):
        x1_1 = x1
        x2_1 = self.conv_upsample1(self.upsample(x1)) * x2
        x3_1 = self.conv_upsample2(self.upsample(self.upsample(x1))) \
               * self.conv_upsample3(self.upsample(x2)) * x3

        x2_2 = torch.cat((x2_1, self.conv_upsample4(self.upsample(x1_1))), 1)
        x2_2 = self.conv_concat2(x2_2)

        x3_2 = torch.cat((x3_1, self.conv_upsample5(self.upsample(x2_2))), 1)
        x3_2 = self.conv_concat3(x3_2)

        x = self.conv4(x3_2)
        x = self.conv5(x)

        return x


class Inf_Net(nn.Module):
    def __init__(self, channel=32, n_class=1):
        super(Inf_Net, self).__init__()
        # ---- ResNet Backbone ----
        self.resnet = res2net50_v1b_26w_4s(pretrained=True)
        # ---- Receptive Field Block like module ----
        self.rfb2_1 = RFB_modified(512, channel)
        self.rfb3_1 = RFB_modified(1024, channel)
        self.rfb4_1 = RFB_modified(2048, channel)

        # ---- Partial Decoder ----
        self.ParDec = aggregation(channel, n_class)

        # ---- reverse attention branch 4 ----
        self.ra4_conv1 = BasicConv2d(2048, 256, kernel_size=1)
        self.ra4_conv2 = BasicConv2d(256+64, 256, kernel_size=5, padding=2)
        self.ra4_conv3 = BasicConv2d(256, 256, kernel_size=5, padding=2)
        self.ra4_conv4 = BasicConv2d(256, 256, kernel_size=5, padding=2)
        self.ra4_conv5 = BasicConv2d(256, n_class, kernel_size=1)
        # ---- reverse attention branch 3 ----
        self.ra3_conv1 = BasicConv2d(1024, 64, kernel_size=1)
        self.ra3_conv2 = BasicConv2d(64+64, 64, kernel_size=3, padding=1)
        self.ra3_conv3 = BasicConv2d(64, 64, kernel_size=3, padding=1)
        self.ra3_conv4 = BasicConv2d(64, n_class, kernel_size=3, padding=1)
        # ---- reverse attention branch 2 ----
        self.ra2_conv1 = BasicConv2d(512, 64, kernel_size=1)
        self.ra2_conv2 = BasicConv2d(64+64, 64, kernel_size=3, padding=1)
        self.ra2_conv3 = BasicConv2d(64, 64, kernel_size=3, padding=1)
        self.ra2_conv4 = BasicConv2d(64, n_class, kernel_size=3, padding=1)

        # ---- edge branch ----
        self.edge_conv1 = BasicConv2d(256, 64, kernel_size=1)
        self.edge_conv2 = BasicConv2d(64, 64, kernel_size=3, padding=1)
        self.edge_conv3 = BasicConv2d(64, 64, kernel_size=3, padding=1)
        self.edge_conv4 = BasicConv2d(64, n_class, kernel_size=3, padding=1)

    def forward(self, x):
        x = self.resnet.conv1(x)
        x = self.resnet.bn1(x)
        x = self.resnet.relu(x)

        # ---- low-level features ----
        x = self.resnet.maxpool(x)      # bs, 64, 88, 88
        x1 = self.resnet.layer1(x)      # bs, 256, 88, 88

        # ---- high-level features ----
        x2 = self.resnet.layer2(x1)     # bs, 512, 44, 44
        x3 = self.resnet.layer3(x2)     # bs, 1024, 22, 22
        x4 = self.resnet.layer4(x3)     # bs, 2048, 11, 11
        x2_rfb = self.rfb2_1(x2)        # channel -> 32
        x3_rfb = self.rfb3_1(x3)        # channel -> 32
        x4_rfb = self.rfb4_1(x4)        # channel -> 32

        # ---- edge guidance ----
        x = self.edge_conv1(x1)
        x = self.edge_conv2(x)
        edge_guidance = self.edge_conv3(x)  # torch.Size([1, 64, 88, 88])
        lateral_edge = self.edge_conv4(edge_guidance)   # NOTES: Sup-2 (bs, 1, 88, 88) -> (bs, 1, 352, 352)
        lateral_edge = F.interpolate(lateral_edge,
                                     scale_factor=4,
                                     mode='bilinear')

        # ---- global guidance ----
        ra5_feat = self.ParDec(x4_rfb, x3_rfb, x2_rfb)
        lateral_map_5 = F.interpolate(ra5_feat,
                                      scale_factor=8,
                                      mode='bilinear')    # NOTES: Sup-1 (bs, 1, 44, 44) -> (bs, 1, 352, 352)

        # ---- reverse attention branch_4 ----
        crop_4 = F.interpolate(ra5_feat, scale_factor=0.25, mode='bilinear')
        x = -1*(torch.sigmoid(crop_4)) + 1  # reverse
        x = x.expand(-1, 2048, -1, -1).mul(x4)
        x = torch.cat((self.ra4_conv1(x), F.interpolate(edge_guidance, scale_factor=1/8, mode='bilinear')), dim=1)
        x = F.relu(self.ra4_conv2(x))
        x = F.relu(self.ra4_conv3(x))
        x = F.relu(self.ra4_conv4(x))
        ra4_feat = self.ra4_conv5(x)
        x = ra4_feat + crop_4   # element-wise addition
        lateral_map_4 = F.interpolate(x,
                                      scale_factor=32,
                                      mode='bilinear')  # NOTES: Sup-2 (bs, 1, 11, 11) -> (bs, 1, 352, 352)

        # ---- reverse attention branch_3 ----
        crop_3 = F.interpolate(x, scale_factor=2, mode='bilinear')
        x = -1*(torch.sigmoid(crop_3)) + 1
        x = x.expand(-1, 1024, -1, -1).mul(x3)
        x = torch.cat((self.ra3_conv1(x), F.interpolate(edge_guidance, scale_factor=1/4, mode='bilinear')), dim=1)
        x = F.relu(self.ra3_conv2(x))
        x = F.relu(self.ra3_conv3(x))
        ra3_feat = self.ra3_conv4(x)
        x = ra3_feat + crop_3
        lateral_map_3 = F.interpolate(x,
                                      scale_factor=16,
                                      mode='bilinear')  # NOTES: Sup-3 (bs, 1, 22, 22) -> (bs, 1, 352, 352)

        # ---- reverse attention branch_2 ----
        crop_2 = F.interpolate(x, scale_factor=2, mode='bilinear')

        x = -1*(torch.sigmoid(crop_2)) + 1
        x = x.expand(-1, 512, -1, -1).mul(x2)
        x = torch.cat((self.ra2_conv1(x), F.interpolate(edge_guidance, scale_factor=1/2, mode='bilinear')), dim=1)
        x = F.relu(self.ra2_conv2(x))
        x = F.relu(self.ra2_conv3(x))
        ra2_feat = self.ra2_conv4(x)
        x = ra2_feat + crop_2
        lateral_map_2 = F.interpolate(x,
                                      scale_factor=8,
                                      mode='bilinear')   # NOTES: Sup-4 (bs, 1, 44, 44) -> (bs, 1, 352, 352)

        return lateral_map_5, lateral_map_4, lateral_map_3, lateral_map_2, lateral_edge


seminet_pth ='Semi-Inf-Net/Semi-Inf-Net-100.pth'
save_test = 'Results/Lung-infection-segmentation/Semi-Inf-Net/'
save_train = 'Results/Lung-infection-segmentation/train/'

semi = Inf_Net()
device = torch.device('cpu')
semi.load_state_dict(torch.load(seminet_pth, map_location=device))
semi.eval()


path = 'Semi-Inf-Net_UNet/unet_model_200.pkl'

import torch
import torch.nn as nn
import torch.nn.functional as F


class DoubleConv(nn.Module):
    """(convolution => [BN] => ReLU) * 2"""

    def __init__(self, in_channels, out_channels, mid_channels=None):
        super().__init__()
        if not mid_channels:
            mid_channels = out_channels
        self.double_conv = nn.Sequential(
            nn.Conv2d(in_channels, mid_channels, kernel_size=3, padding=1),
            nn.BatchNorm2d(mid_channels),
            nn.ReLU(inplace=True),
            nn.Conv2d(mid_channels, out_channels, kernel_size=3, padding=1),
            nn.BatchNorm2d(out_channels),
            nn.ReLU(inplace=True)
        )

    def forward(self, x):
        return self.double_conv(x)


class Down(nn.Module):
    """Downscaling with maxpool then double conv"""

    def __init__(self, in_channels, out_channels):
        super().__init__()
        self.maxpool_conv = nn.Sequential(
            nn.MaxPool2d(2),
            DoubleConv(in_channels, out_channels)
        )

    def forward(self, x):
        return self.maxpool_conv(x)


class Up(nn.Module):
    """Upscaling then double conv"""

    def __init__(self, in_channels, out_channels, bilinear=True):
        super().__init__()

        # if bilinear, use the normal convolutions to reduce the number of channels
        if bilinear:
            self.up = nn.Upsample(scale_factor=2, mode='bilinear', align_corners=True)
            self.conv = DoubleConv(in_channels, out_channels, in_channels // 2)
        else:
            self.up = nn.ConvTranspose2d(in_channels , in_channels // 2, kernel_size=2, stride=2)
            self.conv = DoubleConv(in_channels, out_channels)


    def forward(self, x1, x2):
        x1 = self.up(x1)
        # input is CHW
        diffY = x2.size()[2] - x1.size()[2]
        diffX = x2.size()[3] - x1.size()[3]

        x1 = F.pad(x1, [diffX // 2, diffX - diffX // 2,
                        diffY // 2, diffY - diffY // 2])
        # if you have padding issues, see
        # https://github.com/HaiyongJiang/U-Net-Pytorch-Unstructured-Buggy/commit/0e854509c2cea854e247a9c615f175f76fbb2e3a
        # https://github.com/xiaopeng-liao/Pytorch-UNet/commit/8ebac70e633bac59fc22bb5195e513d5832fb3bd
        x = torch.cat([x2, x1], dim=1)
        return self.conv(x)


class OutConv(nn.Module):
    def __init__(self, in_channels, out_channels):
        super(OutConv, self).__init__()
        self.conv = nn.Conv2d(in_channels, out_channels, kernel_size=1)

    def forward(self, x):
        return self.conv(x)

class Inf_Net_UNet(nn.Module):
    """ Full assembly of the parts to form the complete network """
    def __init__(self, n_channels, n_classes, bilinear=True):
        super(Inf_Net_UNet, self).__init__()
        self.n_channels = n_channels
        self.n_classes = n_classes
        self.bilinear = bilinear

        self.inc = DoubleConv(n_channels, 64)
        self.down1 = Down(64, 128)
        self.down2 = Down(128, 256)
        self.down3 = Down(256, 512)
        factor = 2 if bilinear else 1
        self.down4 = Down(512, 1024 // factor)
        self.up1 = Up(1024, 512 // factor, bilinear)
        self.up2 = Up(512, 256 // factor, bilinear)
        self.up3 = Up(256, 128 // factor, bilinear)
        self.up4 = Up(128, 64, bilinear)
        self.outc = OutConv(64, n_classes)

    def forward(self, x):
        x1 = self.inc(x)
        x2 = self.down1(x1)
        x3 = self.down2(x2)
        x4 = self.down3(x3)
        x5 = self.down4(x4)
        x = self.up1(x5, x4)
        x = self.up2(x, x3)
        x = self.up3(x, x2)
        x = self.up4(x, x1)
        logits = self.outc(x)

        return logits

infnet = Inf_Net_UNet(6,3)
device = torch.device('cpu')
infnet.load_state_dict(torch.load(path, map_location=device))


Inf_Net_UNet(
  (inc): DoubleConv(
    (double_conv): Sequential(
      (0): Conv2d(6, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU(inplace=True)
      (3): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (4): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (5): ReLU(inplace=True)
    )
  )
  (down1): Down(
    (maxpool_conv): Sequential(
      (0): MaxPool2d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
      (1): DoubleConv(
        (double_conv): Sequential(
          (0): Conv2d(64, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
          (1): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (2): ReLU(inplace=True)
          (3): Conv2d(128, 128, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
          (4): BatchNorm2d(128, eps=1e-05

In [ ]:
semi.eval()
infnet.eval()

In [6]:
def bound_box_and_reshape(img, slice_idx):
    """
    Crop given slice of image to lung size (remove redundant empty space) and reshape to 512x512 pxls. Return edited img_slice.
    """
    img_slice = img[:,:,slice_idx]    
    rows = np.any(img_slice, axis=1)
    cols = np.any(img_slice, axis=0)
    rmin, rmax = np.where(rows)[0][[0, -1]]
    cmin, cmax = np.where(cols)[0][[0, -1]]
    img_slice = resize(img_slice[rmin:rmax, cmin:cmax], (512,512))
    img_slice = np.transpose(img_slice[:, :, np.newaxis], axes = [2, 0, 1]).astype('float32')
    lung_pixels = abs((rmax-rmin) * (cmax - cmin))
    
    return img_slice, lung_pixels

In [7]:
def mask_original(filepath_CT, filepath_mask):
    """
    Mask and normalize original CT. Select only preset number of central slices. 
    """
    I = np.array(nib.load(filepath_CT).dataobj)
    #I = normalize(I, -1350, 150)
    M, _ = nrrd.read(filepath_mask)
    
    nS = np.where(M==1, I, M)
    
    #z = nS.shape[2]//2
    #dz = nb_central_slices//2
    #nS = nS[:,:,z-dz:z+dz]
        
    return nS

In [8]:
def percent_lungs_slice(filepath_mask, slice_number):
    M, _ = nrrd.read(filepath_mask)
    current_slice, _ = bound_box_and_reshape(M, slice_number)
    num_pixels = current_slice.shape[2] * current_slice.shape[1]
    white = np.sum(current_slice)
    return "{:.1f}".format(white / num_pixels)

In [9]:
def get_label(patient_number):
    with open(LABEL_PATH) as file:
        for line in file.readlines():
            if str(patient_number) in line:
                label = line.split(",")[1].rsplit("\n")[0]
                return label

In [10]:
def calculate_mask_area_percentage(mask, NP_VALUE_OF_MASK):
    """
        Input je numpy array. Vrže ven odstotek, kolikšen
        del slike zajema anomalija.
    """
    mask = np.where(mask == NP_VALUE_OF_MASK, 1, 0)
    summa = np.sum(mask)
    percentage = float(summa) / (mask.shape[0]*mask.shape[1])
    return round(percentage,3)

In [30]:
def rgb_loader(path):
    img = Image.open(path)
    #img = img.convert('RGB')
    return img

In [31]:
def transform(x):
    operation = transforms.Compose([
                transforms.Resize((352, 352)),
                transforms.ToTensor(),
                transforms.Normalize([0.485, 0.456, 0.406],
                                    [0.229, 0.224, 0.225])
    ])
    return operation(x).unsqueeze(0)

In [32]:
def predict_semi(k, model = semi):
    lateral_map_5, lateral_map_4, lateral_map_3, lateral_map_2, lateral_edge = model(k)
    res = lateral_map_2
    res = res.sigmoid().data.cpu().numpy().squeeze()
    res = (res - res.min()) / (res.max() - res.min() + 1e-8)
    #plt.imsave(save_path + '0.jpeg' ,res, cmap = 'gray')
    #plt.imshow(res, cmap='gray')
    return res

In [33]:
def predict_unet(k,d):
    s = torch.cat((k,d), dim=1)
    res = infnet(s)
    res = torch.sigmoid(res) 
    b, _, w, h = res.size()
    # output b*n_class*h*w -- > b*h*w
    pred = res.cpu().permute(0, 2, 3, 1).contiguous().view(-1, 3).max(1)[1].view(b, w, h).numpy().squeeze()
    return pred

In [34]:
def split_class_imgs(pred):
    im_array_red = np.array(pred)  # 0, 38
    im_array_green = np.array(pred)  # 0, 75
    print(np.unique(im_array_red)) # mask value is max of this

    im_array_red[im_array_red != 0] = 1
    im_array_red[im_array_red == 0] = 255
    im_array_red[im_array_red == 1] = 0

    im_array_green[im_array_green != 1] = 0
    im_array_green[im_array_green == 1] = 255
    
   # red = Image.fromarray(im_array_red).convert('1').resize(size=(512, 512))
    #green = Image.fromarray(im_array_red).convert('1').resize(size=(512, 512))

    return im_array_green, im_array_red

In [35]:
def process_one_patient(filename_img):
    filename_mask = filename_img.replace(".nii.gz", ".nrrd")
    filepath_img = os.path.join(TRAIN_PATH, filename_img)
    filepath_mask = os.path.join(SEGMENTATION_PATH, filename_mask)
    patient_number = filename_mask.split(".nrrd")[0]
    
    img = mask_original(filepath_img, filepath_mask)
    num_slices = img.shape[2]
    
    label = get_label(patient_number)
    
    patient_lung_volume_score = 0.0
    patient_ggo_score = 0.0
    patient_consolidation_score = 0.0
        
    for i in tqdm(range(num_slices)):
        try:
            current_slice, bbox_pixels = bound_box_and_reshape(img, i)
        except:
            continue
        current_slice = np.rot90(np.squeeze(current_slice))
        percentage = percent_lungs_slice(filepath_mask, i)
        if percentage != 0:
            # lahko v eni rundi kličem in semi in unet
            cur_path = 'slice.jpg'
            semi_path = 'semi.jpg'
            plt.imsave(cur_path, current_slice)
            current_slice = rgb_loader(cur_path)
            seg = transform(current_slice)
            semi_mask = predict_semi(seg, model = semi)
            plt.imsave(semi_path, semi_mask)
            unet_mask = predict_unet(seg, transform(rgb_loader(semi_path)))

            ggo_mask, consolidation_mask = split_class_imgs(unet_mask)
            
            NP_VALUE_OF_MASK = 255
            patient_lung_volume_score += float(percentage) * bbox_pixels
            
            ggo_percentage = calculate_mask_area_percentage(ggo_mask, NP_VALUE_OF_MASK)
            consolidation_percentage = calculate_mask_area_percentage(consolidation_mask, NP_VALUE_OF_MASK)
            
            patient_ggo_score += ggo_percentage * bbox_pixels
            patient_consolidation_score += consolidation_percentage * bbox_pixels
            
            os.remove(cur_path)
            os.remove(semi_path)
            
            
    return {"filename_img" : filename_img,
            "label" : label,
            "lung_vol": patient_lung_volume_score, 
            "ggo_vol" : patient_ggo_score, 
            "cons_vol" : patient_consolidation_score}

In [36]:
filename_img = '0107.nii.gz'

In [37]:
i = 27

In [38]:
filename_mask = filename_img.replace(".nii.gz", ".nrrd")
filepath_img = os.path.join(TRAIN_PATH, filename_img)
filepath_mask = os.path.join(SEGMENTATION_PATH, filename_mask)
patient_number = filename_mask.split(".nrrd")[0]
img = mask_original(filepath_img, filepath_mask)


In [39]:
current_slice, bbox_pixels = bound_box_and_reshape(img, i)
current_slice = np.rot90(np.squeeze(current_slice))
percentage = percent_lungs_slice(filepath_mask, i)

In [40]:
cur_path = 'slice.jpg'
semi_path = 'semi.jpg'
unet_path = 'unet.jpg'
ggo_path = 'ggo.jpg'
conso_path = 'cons.jpg'
plt.imsave(cur_path, current_slice)
current_slice = rgb_loader(cur_path)
seg = transform(current_slice)
semi_mask = predict_semi(seg, model = semi)
plt.imsave(semi_path, semi_mask)
unet_mask = predict_unet(seg, transform(rgb_loader(semi_path)))
plt.imsave(unet_path, unet_mask)

ggo_mask, consolidation_mask = split_class_imgs(unet_mask)
plt.imsave(ggo_path, ggo_mask)

plt.imsave(conso_path, consolidation_mask)


[0 1 2]


In [54]:
x = process_one_patient(filename_img)

  4%|▍         | 3/68 [00:03<01:26,  1.32s/it]

[0 1 2]


  6%|▌         | 4/68 [00:06<01:48,  1.70s/it]

[0 1 2]


  7%|▋         | 5/68 [00:08<01:45,  1.68s/it]

...

[0 1 2]


 91%|█████████ | 62/68 [02:17<00:14,  2.45s/it]

[0 1 2]


100%|██████████| 68/68 [02:19<00:00,  2.06s/it]

[0 1 2]


In [55]:
x

{'filename_img': '0279.nii.gz',
 'label': '0',
 'lung_vol': 1907402.5999999992,
 'ggo_vol': 2881.993,
 'cons_vol': 20629.460999999996}

In [56]:
x['ggo_vol']/x['lung_vol']

0.0015109515945925633

In [57]:
x['cons_vol']/x['lung_vol']

0.010815472832007256

In [110]:
vis_path = 'visual/'
def initdir(filename):
    path = vis_path + filename.replace(".nii.gz", "/")
    if os.path.exists(path):
        shutil.rmtree(path)
    os.makedirs(path)
    return path

In [111]:
initdir(filename_img)

'visual/0321/'

In [112]:
def save_images_one(filename_img):
    k_path = initdir(filename_img)
    filename_mask = filename_img.replace(".nii.gz", ".nrrd")
    filepath_img = os.path.join(TRAIN_PATH, filename_img)
    filepath_mask = os.path.join(SEGMENTATION_PATH, filename_mask)
    patient_number = filename_mask.split(".nrrd")[0]
    
    img = mask_original(filepath_img, filepath_mask)
    num_slices = img.shape[2]
    
    
    
    for i in tqdm(range(num_slices)):
        store_path = k_path + str(i)+"-"
        try:
            current_slice, bbox_pixels = bound_box_and_reshape(img, i)
        except:
            continue
        current_slice = np.rot90(np.squeeze(current_slice))
        percentage = percent_lungs_slice(filepath_mask, i)
        if percentage != 0:
            # lahko v eni rundi kličem in semi in unet
            plt.imsave(store_path+"cur"+".jpg", current_slice)
            current_slice = rgb_loader(store_path+"cur"+".jpg")
            seg = transform(current_slice)
            semi_mask = predict_semi(seg, model = semi)
            plt.imsave(store_path+"semi"+".jpg", semi_mask)
            unet_mask = predict_unet(seg, transform(rgb_loader(store_path+"semi"+".jpg")))
            plt.imsave(store_path+"unet"+".jpg", unet_mask)

            ggo_mask, consolidation_mask = split_class_imgs(unet_mask)
            plt.imsave(store_path+"ggo"+".jpg", ggo_mask)
            plt.imsave(store_path+"conso"+".jpg", consolidation_mask)

In [65]:
#save_images_one(filename_img)

In [106]:
def load_images_from_folder(folder):
    images = []
    for filename in os.listdir(folder):
        img = cv2.imread(os.path.join(folder,filename))
        if img is not None:
            images.append(img)
    return images

In [80]:
def display_by_slice(x, num_slices = 64):
    for k in load_images_from_folder(x):
        plt.imshow(k)

In [89]:
load_images_from_folder('visual/0032/')


[]

In [136]:
#current_slice = transform(img)

In [137]:
#semi_mask = predict_semi(current_slice, model = semi)
#plt.imsave('semi.jpg', semi_mask)

In [138]:
#semi_mask = rgb_loader('semi.jpg')
#plt.imshow(semi_mask, cmap = 'gray')

In [139]:
#semi_mask = transform(semi_mask)

In [140]:
#unet_mask = predict_unet(current_slice, semi_mask)
#plt.imshow(unet_mask, cmap = 'gray')

In [141]:
#ggo_mask, consolidation_mask = split_class_imgs(unet_mask)

In [66]:
#x = process_one_patient(filename_img)

In [143]:
x

{'filename_img': '0032.nii.gz',
 'label': '1',
 'lung_vol': 1369103.3999999997,
 'ggo_vol': 99926.74799999999,
 'cons_vol': 196004.162}

In [42]:
print(x['ggo_vol']/x['lung_vol']*100)

7.581732617832682


In [43]:
print(x['cons_vol']/x['lung_vol']*100)

14.901794519864337


In [67]:
#y = process_one_patient('0533.nii.gz')

In [46]:
print(y['ggo_vol']/y['lung_vol']*100)

6.401189660014406


In [47]:
print(y['cons_vol']/y['lung_vol']*100)

12.55995849110884


In [68]:
training_csv = 'training.csv'

In [71]:
def process_all_patients():
    training_set = []
    for _,_,filenames in os.walk(TRAIN_PATH):
        for filename in tqdm(filenames):
            if filename.endswith(".nii.gz"):
                patient_dict = process_one_patient(filename)
                with open(training_csv, mode='a') as file_:
                    file_.write(str(patient_dict.values()))
                    file_.write("\n")
                training_set.append(patient_dict)
    return training_set

In [72]:
results = process_all_patients()

 10%|▉         | 6/62 [00:02<00:23,  2.36it/s]

[0 1 2]



 11%|█▏        | 7/62 [00:11<01:50,  2.01s/it]

[0 1 2]



 13%|█▎        | 8/62 [00:14<01:59,  2.21s/it]

...

[0 1 2]



 93%|█████████▎| 55/59 [01:44<00:07,  1.81s/it]

[0 1 2]



100%|██████████| 355/355 [13:02:59<00:00, 132.34s/it]

[0 1 2]
